In [26]:
import pandas as pd
import nltk
from nltk.tokenize import word_tokenize
nltk.download('punkt')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\gabri\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping tokenizers\punkt.zip.


True

In [40]:
from gensim.models import Word2Vec
from gensim.models.phrases import Phraser, Phrases
from gensim.test.utils import common_texts

In [8]:
df = pd.read_csv('data/clean_train_data.csv')
df

Unnamed: 0        Id  \
0               0  34552656   
1               1  34553034   
2               2  34553174   
3               3  34553318   
4               4  34553755   
...           ...       ...   
44995       44995  60461435   
44996       44996  60461754   
44997       44997  60462001   
44998       44998  60465318   
44999       44999  60468018   

                                                   Title  \
0                 Java: Repeat Task Every Random Seconds   
1                      Why are Java Optionals immutable?   
2      Text Overlay Image with Darkened Opacity React...   
3             Why ternary operator in swift is so picky?   
4                     hide/show fab with scale animation   
...                                                  ...   
44995  Convert List<String> to string C# - asp.net - ...   
44996  Does Python execute code from the top or botto...   
44997               how to change payment date in Azure?   
44998        how to implement fill in the blank in Swift   
44999  How can I make a c# application outside of vis...   

                                                    Body  \
0      I'm already familiar with repeating tasks ever...   
1      I'd like to understand why Java 8 Optionals we...   
2      I am attempting to overlay a title over an ima...   
3      The question is very simple, but I just could ...   
4      I'm using custom floatingactionmenu. I need to...   
...                                                  ...   
44995  I am new to this and I am asking for help to c...   
44996  I am working on learning Python and was wonder...   
44997  It looks like it costs 8 days per month in Azu...   
44998  "I _____ any questions."I want to implement a ...   
44999  I'm very new to programming and I'm teaching m...   

                                                    Tags         CreationDate  \
0                                            java repeat  2016-01-01 00:21:59   
1                                          java optional  2016-01-01 02:03:20   
2          javascript image overlay react-native opacity  2016-01-01 02:48:24   
3      swift operators whitespace ternary-operator op...  2016-01-01 03:30:17   
4         android material-design floating-action-button  2016-01-01 05:21:48   
...                                                  ...                  ...   
44995                              c# asp.net sql-server  2020-02-29 02:22:18   
44996                                             python  2020-02-29 03:33:59   
44997                                      azure billing  2020-02-29 04:34:16   
44998                                          ios swift  2020-02-29 12:50:43   
44999                                   c# visual-studio  2020-02-29 17:55:56   

              Y  
0      LQ_CLOSE  
1            HQ  
2            HQ  
3            HQ  
4            HQ  
...         ...  
44995  LQ_CLOSE  
44996  LQ_CLOSE  
44997  LQ_CLOSE  
44998  LQ_CLOSE  
44999  LQ_CLOSE  

[45000 rows x 7 columns]

In [16]:
df['Title']

0                   Java: Repeat Task Every Random Seconds
1                        Why are Java Optionals immutable?
2        Text Overlay Image with Darkened Opacity React...
3               Why ternary operator in swift is so picky?
4                       hide/show fab with scale animation
                               ...                        
44995    Convert List<String> to string C# - asp.net - ...
44996    Does Python execute code from the top or botto...
44997                 how to change payment date in Azure?
44998          how to implement fill in the blank in Swift
44999    How can I make a c# application outside of vis...
Name: Title, Length: 45000, dtype: object

In [19]:
title = list(df['Title'])
body = list(df['Body'])
df['full_text'] = [f"{title[i]} {body[i]}" for i in range(len(title))]

In [21]:
df['full_text']

0        Java: Repeat Task Every Random Seconds I'm alr...
1        Why are Java Optionals immutable? I'd like to ...
2        Text Overlay Image with Darkened Opacity React...
3        Why ternary operator in swift is so picky? The...
4        hide/show fab with scale animation I'm using c...
                               ...                        
44995    Convert List<String> to string C# - asp.net - ...
44996    Does Python execute code from the top or botto...
44997    how to change payment date in Azure? It looks ...
44998    how to implement fill in the blank in Swift "I...
44999    How can I make a c# application outside of vis...
Name: full_text, Length: 45000, dtype: object

In [27]:
full_text = list(df['full_text'])
tokenized_sents = [word_tokenize(s) for s in full_text]

In [31]:
tokenized_sents

[['Java',
  ':',
  'Repeat',
  'Task',
  'Every',
  'Random',
  'Seconds',
  'I',
  "'m",
  'already',
  'familiar',
  'with',
  'repeating',
  'tasks',
  'every',
  'n',
  'seconds',
  'by',
  'using',
  'Java.util.Timer',
  'and',
  'Java.util.TimerTask',
  '.',
  'But',
  'lets',
  'say',
  'I',
  'want',
  'to',
  'print',
  '``',
  'Hello',
  'World',
  "''",
  'to',
  'the',
  'console',
  'every',
  'random',
  'seconds',
  'from',
  '1-5',
  '.',
  'Unfortunately',
  'I',
  "'m",
  'in',
  'a',
  'bit',
  'of',
  'a',
  'rush',
  'and',
  'do',
  "n't",
  'have',
  'any',
  'code',
  'to',
  'show',
  'so',
  'far',
  '.',
  'Any',
  'help',
  'would',
  'be',
  'apriciated',
  '.'],
 ['Why',
  'are',
  'Java',
  'Optionals',
  'immutable',
  '?',
  'I',
  "'d",
  'like',
  'to',
  'understand',
  'why',
  'Java',
  '8',
  'Optionals',
  'were',
  'designed',
  'to',
  'be',
  'immutable',
  '.',
  'Is',
  'it',
  'just',
  'for',
  'thread-safety',
  '?'],
 ['Text',
  'Overlay

In [36]:
# Phrase Detection
# Give some common terms that can be ignored in phrase detection
# For example, 'state_of_affairs' will be detected because 'of' is provided here: 
common_terms = ["of", "with", "without", "and", "or", "the", "a"]
# Create the relevant phrases from the list of sentences:
phrases = Phrases(tokenized_sents)
# The Phraser object is used from now on to transform sentences
bigram = Phraser(phrases)
# Applying the Phraser to transform our sentences is simply
all_sentences = list(bigram[tokenized_sents])

In [37]:
all_sentences

[['Java',
  ':',
  'Repeat',
  'Task',
  'Every',
  'Random',
  'Seconds',
  "I_'m",
  'already',
  'familiar_with',
  'repeating',
  'tasks',
  'every',
  'n',
  'seconds',
  'by',
  'using',
  'Java.util.Timer',
  'and',
  'Java.util.TimerTask',
  '._But',
  'lets_say',
  'I_want',
  'to',
  'print',
  '``',
  'Hello_World',
  "''",
  'to',
  'the',
  'console',
  'every',
  'random',
  'seconds',
  'from',
  '1-5',
  '.',
  'Unfortunately',
  "I_'m",
  'in',
  'a_bit',
  'of',
  'a',
  'rush',
  'and',
  "do_n't",
  'have',
  'any',
  'code',
  'to',
  'show',
  'so_far',
  '._Any',
  'help_would',
  'be',
  'apriciated',
  '.'],
 ['Why',
  'are',
  'Java',
  'Optionals',
  'immutable',
  '?',
  "I_'d",
  'like',
  'to',
  'understand_why',
  'Java_8',
  'Optionals',
  'were',
  'designed',
  'to',
  'be',
  'immutable',
  '.',
  'Is_it',
  'just',
  'for',
  'thread-safety',
  '?'],
 ['Text',
  'Overlay',
  'Image',
  'with',
  'Darkened',
  'Opacity',
  'React_Native',
  'I_am',
 

In [65]:
model = Word2Vec(sentences=all_sentences, vector_size=1000, window=17, min_count=1, workers=4)

In [66]:
model.wv.most_similar('php', topn=10)

[('PHP', 0.8885607719421387),
 ('mysqli', 0.7341732978820801),
 ('javascript', 0.7302075028419495),
 ('laravel', 0.7254460453987122),
 ('Php', 0.7230034470558167),
 ('phpmyadmin', 0.7155064940452576),
 ('ajax', 0.7142506837844849),
 ('perl', 0.7065373063087463),
 ('mysql', 0.698390543460846),
 ('mail', 0.689083456993103)]

In [54]:
model.wv.vocab

AttributeError: The vocab attribute was removed from KeyedVector in Gensim 4.0.0.
Use KeyedVector's .key_to_index dict, .index_to_key list, and methods .get_vecattr(key, attr) and .set_vecattr(key, attr, new_val) instead.
See https://github.com/RaRe-Technologies/gensim/wiki/Migrating-from-Gensim-3.x-to-4

In [62]:
model.wv.index_to_key

[')',
 '(',
 ',',
 ':',
 "''",
 ';',
 'the',
 '``',
 'to',
 '=',
 '.',
 '{',
 '}',
 'a',
 '>',
 ']',
 'in',
 "'",
 '[',
 'I',
 'and',
 'is',
 '?',
 '<',
 'of',
 'this',
 'i',
 'it',
 'for',
 '$',
 'that',
 'with',
 '1',
 'if',
 '0',
 'but',
 'from',
 '*',
 'my',
 'on',
 '-',
 'I_have',
 'int',
 '*_*',
 'code',
 '`',
 '2',
 'using',
 '!',
 'not',
 '+',
 '--_--',
 'as',
 'return',
 'or',
 'get',
 'I_am',
 'do',
 'new',
 'function',
 'use',
 'when',
 'have',
 "I_'m",
 'at',
 '#',
 'data',
 'can',
 'string',
 '/',
 'error',
 '//',
 'How',
 'file',
 'an',
 'how',
 '@',
 'I_want',
 '3',
 'value',
 'String',
 'The',
 'name',
 'which',
 'all',
 'class',
 'are',
 'so',
 '...',
 'one',
 '--',
 '%',
 'be',
 'what',
 'var',
 'like',
 'print',
 'x',
 '==',
 '&',
 'some',
 'array',
 'by',
 'android',
 'list',
 'trying_to',
 'you',
 'type',
 'public',
 "'s",
 'only',
 'there',
 'https_:',
 'import',
 'line',
 'way',
 '4',
 'make',
 'me',
 '|',
 'just',
 '10',
 'user',
 'run',
 '5',
 'set',
 'here',
 